## Import necessary libraries and packages
Pmport Python libraries required for data manipulation, visualization, and app creation. Key libraries include pandas (for data handling), numpy (for numerical operations), matplotlib (for plotting), and Dash (for interactive dashboards).

In [194]:
import pandas as pd
import numpy as np
from datetime import datetime, timedelta
import swcol as sc

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots

from dash import Dash, dcc, html, Input, Output

## Define input variables
Initialize file paths to load and save data for the dispatch model and sets a base year for filtering data. These constants ensure consistency across the analysis.

In [195]:
model_inputs_path = '../../model/inputs/'
model_outputs_path = '../../model/outputs/'
data_path = '../../data/XM-API/variable_query/2022-12-01_2023-11-30/'

base_year = '2023'

## Load timepoints

In [196]:
timepoints = pd.read_csv(model_inputs_path+'timepoints.csv')

## Load dispatch data from Switch

In [197]:
gen_disp = pd.read_csv(model_outputs_path+'dispatch.csv')
# Get only timepoints from 2023
gen_disp['year'] = gen_disp['timestamp'].str[:4]
gen_disp = gen_disp[gen_disp['year'] == base_year]
# Join the timepoint according to the timestamp
gen_disp = pd.merge(gen_disp, timepoints, on='timestamp', how='inner')

gen_disp = gen_disp[['timepoint_id','timestamp','gen_dbid','DispatchGen_MW']]
gen_disp.sample(3)

timepoint_id         timestamp      gen_dbid  DispatchGen_MW
8549           102  2023_Q3_labor_5h  H_CascadaAnt        1.734853
7060           149  2023_Q4_labor_4h      H_Bayona        0.354547
9752           153  2023_Q4_labor_8h    H_Coconuco        1.584793

## Load dispatch data from XM

In [198]:
# Creamos un rango de fechas con granularidad horaria
start_date = datetime(2022, 12, 1)
end_date = start_date + timedelta(days=365)
date_range = pd.date_range(start=start_date, end=end_date, freq='h')

date_to_timestamp = sc.rain_seasons.format_hours(pd.DataFrame({'Date': date_range}))
date_to_timestamp.drop(date_to_timestamp.tail(1).index,inplace=True)

date_to_timestamp.sample(3)

Date            timestamp
1197 2023-01-19 21:00:00    2023_Q1_labor_21h
5286 2023-07-09 06:00:00  2023_Q3_holidays_6h
8050 2023-11-01 10:00:00    2023_Q4_labor_10h

In [199]:
# Get generation
gen_res = pd.read_csv(data_path+'Gene_Recurso.csv')
gen_res = gen_res.drop(gen_res.columns[0], axis=1)
# Get the list of resources
lis_res = pd.read_csv(data_path+'LitadoRecursos_Sistema.csv')
lis_res = lis_res[['Values_Code','Values_Name']]
# Join the generation with the respective resource
gen_res = pd.merge(
    gen_res, lis_res, left_on='Values_code', right_on='Values_Code', how='inner')
# Get the Switch-XM Map
xm_map = pd.read_csv(data_path+'Map.csv')
# Join the xm projects with switch names.
gen_res = pd.merge(
    gen_res, xm_map, on='Values_Name', how='inner')
gen_res = gen_res.drop(columns=['Id', 'Values_code', 'Values_Name'])
# Melt values into rows
gen_res = pd.melt(
    gen_res, id_vars=['GENERATION_PROJECT', 'Date'],
    value_vars=[f'Values_Hour{i:02}' for i in range(1, 25)], 
    var_name='Hour', value_name='Value')
# Fill NA values with 0's
gen_res = gen_res.fillna(0)
# Convert values from KW to MW
gen_res['Value'] = gen_res['Value'] / 1000

# Convert into timestamps
gen_res['Hour'] = gen_res['Hour'].apply(sc.rain_seasons.extract_hour)
gen_res['Date'] = gen_res['Date'].astype(str)
gen_res['Date'] = gen_res['Date'] + ' ' + gen_res['Hour']
gen_res['Date'] = pd.to_datetime(gen_res['Date'])
# Remove 'Hour' column
gen_res = gen_res.drop(columns=['Hour'])

#print("Generation by resource (XM) shape: ",gen_res.shape)
gen_res = gen_res.groupby(['Date','GENERATION_PROJECT']).agg({
    'Value': 'sum'}).reset_index()

print("Generation by resource (XM) shape: ",gen_res.shape)
gen_res.sample(3)

Generation by resource (XM) shape:  (1930968, 3)


Date GENERATION_PROJECT    Value
223977  2023-01-15 13:00:00        H_Municipal  0.00276
1150886 2023-07-14 20:00:00        H_Municipal  1.24977
863244  2023-05-23 14:00:00       H_ProvidencI  5.96870

In [200]:
# Generate all the possible dates and projects to fill up the non existant values
all_comb = pd.MultiIndex.from_product(
    [date_to_timestamp['Date'], gen_res['GENERATION_PROJECT'].unique()], names=['Date', 'GENERATION_PROJECT']).to_frame(index=False)
print(all_comb.shape)
# Add the timestamp based on the date
all_comb = all_comb.merge(date_to_timestamp, on='Date', how='left')
# Add the missing dates
gen_res = pd.merge(all_comb, gen_res, on=['Date', 'GENERATION_PROJECT'], how='left')
print(gen_res.shape)
# Fill missing data with 0
gen_res['Value'] = gen_res['Value'].fillna(0)

gen_res.sample(3)

(2470320, 2)
(2470320, 4)


Date GENERATION_PROJECT         timestamp      Value
605105  2023-02-28 09:00:00       TERMO YOPAL2  2023_Q1_labor_9h    0.00000
1483734 2023-07-08 05:00:00           SOGAMOSO  2023_Q3_labor_5h  616.62399
468234  2023-02-08 04:00:00             H_Zeus  2023_Q1_labor_4h    2.71461

## Compare System Dispatch from Switch with XM

In [201]:
# Generation from XM
plot_res = gen_res.copy()
plot_res = plot_res.groupby(['Date']).agg({
    'Value': 'sum', 'timestamp':'max'}).reset_index()
plot_res = plot_res.groupby(['timestamp']).agg({
    'Value': 'mean', 'Date':'max'}).reset_index()

plot_res = pd.merge(
    plot_res, timepoints, on='timestamp', how='inner')
plot_res = plot_res.sort_values(by='timepoint_id')
plot_res = plot_res[['timestamp','Value']]
plot_res['Data'] = 'XM'

plot_res.head(3)

timestamp        Value Data
24  2023_Q1_labor_0h  8575.147389   XM
35  2023_Q1_labor_1h  8100.345904   XM
40  2023_Q1_labor_2h  7824.944627   XM

In [202]:
# Generation from Switch
plot_disp = gen_disp.copy()
plot_disp.rename(columns={'gen_dbid': 'GENERATION_PROJECT', 'DispatchGen_MW':'Value'}, inplace=True)
plot_disp = plot_disp.groupby(['timepoint_id']).agg({
    'Value': 'sum', 'timestamp':'max'}).reset_index()
plot_disp = plot_disp.groupby(['timestamp']).agg({
    'Value': 'mean',
    'timepoint_id':'max'}).reset_index()

plot_disp = plot_disp.sort_values(by='timepoint_id')
plot_disp = plot_disp[['timestamp','Value']]
plot_disp['Data'] = 'Switch'

plot_disp.head(3)

timestamp        Value    Data
24  2023_Q1_labor_0h  8591.716752  Switch
35  2023_Q1_labor_1h  8118.571201  Switch
40  2023_Q1_labor_2h  7845.680330  Switch

In [203]:
plot_melt = pd.concat([plot_res, plot_disp])
fig = px.line(plot_melt, x='timestamp', y='Value',color='Data')
#print(plot_res['Value'].sum())
#print(plot_disp['Value'].sum())
fig.show()

In [204]:
gen_info = pd.read_csv(model_inputs_path+'gen_info.csv')
parse_tech = {'Eolica': 'Eolica', 'Thermal': 'Thermal', 'pv_solar': 'Solar', 'Hidro': 'Hydro', 'Menores': 'Hydro Minors'}

# Prepare data for generarion from XM, Add tech column
gen_res = gen_res.groupby(['timestamp','GENERATION_PROJECT']).agg({'Value': 'mean'}).reset_index()
gen_res = gen_res[['timestamp', 'GENERATION_PROJECT', 'Value']]
gen_res = pd.merge(gen_res, gen_info, on='GENERATION_PROJECT', how='inner')
gen_res = pd.merge(gen_res, timepoints, on='timestamp', how='inner')
gen_res = gen_res.sort_values(by='timepoint_id', ascending=True)
gen_res = gen_res[['timestamp', 'GENERATION_PROJECT', 'Value', 'gen_tech']]
gen_res['gen_tech'] = gen_res['gen_tech'].replace(parse_tech)

# Prepare data for generarion from Switch, Add tech column
gen_disp = gen_disp[['timestamp', 'gen_dbid', 'DispatchGen_MW']]
gen_disp = pd.merge(gen_disp, gen_info, left_on='gen_dbid', right_on='GENERATION_PROJECT', how='inner')
gen_disp = pd.merge(gen_disp, timepoints, on='timestamp', how='inner')
gen_disp = gen_disp.sort_values(by='timepoint_id', ascending=True)
gen_disp = gen_disp[['timestamp', 'gen_dbid', 'DispatchGen_MW', 'gen_tech']]
gen_disp['gen_tech'] = gen_disp['gen_tech'].replace(parse_tech)

tech_colors = {'Eolica': '#45CFFF', 'Thermal': '#E84A59', 'Solar': '#EFB52D', 'Hydro': '#744FD0', 'Hydro Minors': '#AEE83C'}

# Initialize Dash app
app = Dash(__name__)

app.layout = html.Div(
    style={'backgroundColor': 'white', 'padding': '20px'},  # Set background color and add padding
    children=[
        html.H1(
            "Dispatch XM vs Switch "+base_year+" (MW)", 
            style={'textAlign': 'center', 'color': 'black'}
        ),
        dcc.Input(
            id='search-input',
            type='text',
            placeholder='Search by Generator...',
            style={
                'margin-bottom': '0px', 
                'width': '300px', 
                'padding': '0px', 
                'border': '1px solid lightgray'
            }
        ),
        dcc.Graph(id='dispatch-graph')
    ])

@app.callback(
    Output('dispatch-graph', 'figure'),
    [Input('search-input', 'value')]
)
def update_graph(search_query):
    # Filter data based on the search query
    if search_query:
        filtered_res = gen_res[gen_res['GENERATION_PROJECT'].str.contains(search_query, case=False, na=False)]
        filtered_disp = gen_disp[gen_disp['gen_dbid'].str.contains(search_query, case=False, na=False)]
    else:
        filtered_res = gen_res
        filtered_disp = gen_disp

    # Create individual plots
    fig1 = px.line(filtered_res, x='timestamp', y='Value', color='GENERATION_PROJECT', title='Generators (XM)')
    fig2 = px.line(filtered_disp, x='timestamp', y='DispatchGen_MW', color='gen_dbid', title='Generators (Switch)')

    # Create subplots
    fig = make_subplots(rows=1, cols=2, subplot_titles=("Generators (XM)", "Generators (Switch)"))

    # Add figures to subplots
    for trace in fig1['data']:
        project_name = trace.name
        technology = filtered_res[filtered_res['GENERATION_PROJECT'] == project_name]['gen_tech'].iloc[0]
        trace.line.color = tech_colors.get(technology, 'black')
        fig.add_trace(trace, row=1, col=1)

    for trace in fig2['data']:
        project_name = trace.name
        technology = filtered_disp[filtered_disp['gen_dbid'] == project_name]['gen_tech'].iloc[0]
        trace.line.color = tech_colors.get(technology, 'black')
        fig.add_trace(trace, row=1, col=2)

    # Show legend to filter only once
    names = set()
    for trace in fig['data']:
        if trace.name in names:
            trace.showlegend = False
        else:
            names.add(trace.name)

    fig.update_layout(
        plot_bgcolor='white',
        xaxis=dict(showgrid=True, gridcolor='lightgray'), yaxis=dict(showgrid=True, gridcolor='lightgray'),
        xaxis2=dict(showgrid=True, gridcolor='lightgray'), yaxis2=dict(showgrid=True, gridcolor='lightgray')
    )
    return fig

# Run the app
app.run_server(mode="inline", debug=False)

In [205]:
aux_disp = gen_disp.copy()
# Group dispatch from Switch
aux_disp['Quarter'] = aux_disp['timestamp'].astype(str).str[0:7]
disp_sw = aux_disp.groupby(['Quarter','gen_dbid','gen_tech']).agg(
    {'DispatchGen_MW': 'sum'}).reset_index()
disp_sw.rename(columns={'gen_dbid': 'GENERATION_PROJECT'}, inplace=True)
disp_sw['Data'] = 'Switch'

# Group dispatch from XM
aux_res = gen_res.copy()
aux_res['Quarter'] = aux_res['timestamp'].astype(str).str[0:7]
disp_xm = aux_res.groupby(['Quarter','GENERATION_PROJECT','gen_tech']).agg(
    {'Value': 'sum'}).reset_index()
disp_xm.rename(columns={'Value': 'DispatchGen_MW'}, inplace=True)
disp_xm['Data'] = 'XM'
tech_x_gen = pd.concat([disp_sw, disp_xm])
tech_x_gen = tech_x_gen.sort_values(by='DispatchGen_MW')

# Show the dispatch side by side
difference = pd.merge(disp_sw, disp_xm, on=['Quarter','GENERATION_PROJECT','gen_tech'])

fig = px.bar(
    tech_x_gen, 
    x="gen_tech", y="DispatchGen_MW",
    color='Data', barmode='group',
    facet_col='Quarter', facet_col_wrap=2,
    hover_name='GENERATION_PROJECT',
    height=650, width=1024,
    title='Comparission in the dispatch per Generation Plant.',
    labels={
        "DispatchGen_MW": "Dispatch per Gen. Plant (MW)", 
        "Data": "Dataset", 
        "gen_tech": "Generation Technologies"
    }
)

fig.show()

In [206]:
difference['diff_switch'] = difference['DispatchGen_MW_x'] - difference['DispatchGen_MW_y']
difference = difference.sort_values(by=['Quarter', 'diff_switch'], ascending=[True, True])

fig = px.bar(
    difference, x="gen_tech", y="diff_switch",
    color='diff_switch',
    barmode='group',
    facet_col='Quarter',
    facet_col_wrap=2,
    hover_name='GENERATION_PROJECT',
    height=650, width=1024,
    title='Difference in the dispatch XM - Switch',
    labels={
        "diff_switch": "Difference in dispatch (MW)",
        "gen_tech": "Generation Technologies"
    }
)

fig.show()

In [207]:
# Join dispatch between XM and Switch
error_disp = pd.merge(gen_res, gen_disp,
                      left_on=['timestamp','GENERATION_PROJECT'],
                      right_on=['timestamp','gen_dbid'],how='inner')
error_disp = error_disp[['timestamp','GENERATION_PROJECT','Value','DispatchGen_MW','gen_tech_x']]
# Remove values below 0.1 to prevent division by a small number
error_disp= error_disp[error_disp['Value'] >= 0.1]
# Calculate the error
error_disp['Error'] = error_disp['DispatchGen_MW'] / error_disp['Value'] - 1
error_disp['Error_abs'] = abs(error_disp['Error'])
error_disp.sample(3)

timestamp GENERATION_PROJECT      Value  DispatchGen_MW  \
19815  2023_Q2_holidays_10h       H_Guanaquita   7.711979        7.997127   
25002      2023_Q3_labor_8h         H_ElBosque   1.580892        1.775580   
10084  2023_Q1_holidays_18h             INSULA  13.760275       12.377302   

         gen_tech_x     Error  Error_abs  
19815  Hydro Minors  0.036975   0.036975  
25002         Hydro  0.123151   0.123151  
10084         Hydro -0.100505   0.100505

In [208]:
# Load capacity to 
capacity = pd.read_csv(model_inputs_path+'gen_build_predetermined.csv')
err_x_cap = pd.merge(error_disp, capacity, on='GENERATION_PROJECT', how='inner')
err_x_cap.rename(
    columns={'timestamp': 'Timestamp', 'gen_tech_x': 'Tech',
             'build_gen_predetermined': 'Capacity'}, inplace=True)
# Only keep these columns
err_x_cap = err_x_cap[['Timestamp','GENERATION_PROJECT','Tech','Value','Error','Error_abs','Capacity']]

def plot_err_x_cap(df, granularity):
    fig = px.scatter(
        df, x='Error', y='Capacity',
        color='Tech', color_discrete_map=tech_colors,
        labels={
            'GENERATION_PROJECT': 'Generation Project', },
        hover_data=['GENERATION_PROJECT',granularity],
        symbol='GENERATION_PROJECT',
        title='Capacity of the Error for '+granularity)
    fig.show()

plot_err_x_cap(err_x_cap, 'Timestamp')

In [209]:
# Meassure by Quarters, group from timestamps
err_x_cap_Q = err_x_cap.copy()
err_x_cap_Q['Quarter'] = err_x_cap_Q['Timestamp'].apply(lambda x: x[:7])
err_x_cap_Q = err_x_cap_Q[err_x_cap_Q['Quarter'].isin([base_year+'_Q1',base_year+'_Q2'])]
## Weigthed Final Error
err_x_cap_Q['Error'] = err_x_cap_Q['Error'] * err_x_cap_Q['Value']
err_x_cap_Q = err_x_cap_Q.groupby(['Quarter','GENERATION_PROJECT','Tech']).agg({
    'Error': 'sum', 'Capacity' : 'mean', 'Value' : 'sum'
}).reset_index()
err_x_cap_Q['Error'] = err_x_cap_Q['Error'] / err_x_cap_Q['Value']

plot_err_x_cap(err_x_cap_Q, 'Quarter')

In [210]:
# Meassure by Year, group from timestamps
err_x_cap_year = err_x_cap.copy()
err_x_cap_year = err_x_cap_year.groupby(['GENERATION_PROJECT','Tech']).agg({
    'Error': 'mean', 'Capacity' : 'mean'
}).reset_index()
err_x_cap_year[base_year] = base_year
plot_err_x_cap(err_x_cap_year, base_year)

In [211]:
# Calculate the general error
general_error = err_x_cap.copy()
general_error['weight'] = 1
general_error['Error'] = general_error['Error'] * general_error['Value']
general_error = general_error.groupby(['weight']).agg({
    'Error': 'sum','Capacity' : 'mean','Value' : 'sum'
}).reset_index()
general_error['Error'] = general_error['Error'] / general_error['Value']

print(f"General Error {general_error['Error'][0]*100:.2f}%")

General Error 1.51%
